In [1]:
import numpy as np
import pandas as pd
from pytz import all_timezones

In [2]:
data_raw = pd.read_csv('crop_data.csv')

In [3]:
data_raw.head()

INDEX                          PROBE_ID          SAMPLE_DATE        LAT  \
0      1                          24046157  2018-06-01 00:57:59  33.808750   
1     13                        4644114056  2018-06-01 00:58:50  33.790882   
2     18  5c3d03bf4888e7c27bb1da53f4b6b4e2  2018-06-01 00:59:22  33.811665   
3     21                        0C01B72E00  2018-06-01 00:59:20  33.812690   
4     30                        0C03CB7B00  2018-06-01 00:59:16  33.715950   

         LONG  HEADING     SPEED PROBE_DATA_PROVIDER              X  \
0 -118.298480    182.0  73.00000             FLEET51  379816.173355   
1 -118.140198    348.0   0.00000             FLEET44  394445.225261   
2 -118.176650     89.0   0.00000             FLEET05  391096.765695   
3 -118.139160      3.0  41.84284             FLEET41  394568.037470   
4 -118.006730    178.0   8.04670             FLEET41  406720.503841   

              Y                 LOCAL_TIME  
0  3.741709e+06  2018-05-31 17:57:59 -0700  
1  3.739554e+06  2018-05-31 17:58:50 -0700  
2  3.741896e+06  2018-05-31 17:59:22 -0700  
3  3.741971e+06  2018-05-31 17:59:20 -0700  
4  3.731117e+06  2018-05-31 17:59:16 -0700

In [4]:
print('unique ID count',len(data_raw.PROBE_DATA_PROVIDER.unique()))
print('unique Probe_ID count',len(data_raw.PROBE_ID.unique()))
print('raw data shape',data_raw.shape)


unique ID count 21
unique Probe_ID count 23979
raw data shape (1989370, 11)


In [5]:
test_date = data_raw['LOCAL_TIME']
data_raw['LOCAL_TIME'] = pd.to_datetime(test_date)
data_raw['LOCAL_TIME'] = data_raw['LOCAL_TIME'].dt.tz_localize('Etc/UTC')
data_raw['LOCAL_TIME'] = data_raw['LOCAL_TIME'].dt.tz_convert('America/Los_Angeles')
data_raw['unix_time'] = pd.DatetimeIndex ( data_raw.LOCAL_TIME ).astype ( np.int64 )//10**9

In [26]:
fleets = set(data_raw.PROBE_DATA_PROVIDER)
fleets

{'CONSUMER05',
 'CONSUMER10',
 'CONSUMER14',
 'CONSUMER15',
 'CONSUMER16',
 'CONSUMER18',
 'CONSUMER21',
 'CONSUMER24',
 'CONSUMER26',
 'FLEET05',
 'FLEET24',
 'FLEET30',
 'FLEET33',
 'FLEET40',
 'FLEET41',
 'FLEET42',
 'FLEET44',
 'FLEET51',
 'FLEET53',
 'FLEET54',
 'FLEET55'}

In [8]:
FLEET51 = data_raw.loc[data_raw.PROBE_DATA_PROVIDER=='FLEET51']
FLEET51.head()


INDEX  PROBE_ID          SAMPLE_DATE        LAT        LONG  HEADING  \
0       1  24046157  2018-06-01 00:57:59  33.808750 -118.298480    182.0   
9      74  18302330  2018-06-01 00:59:08  33.858827 -118.284822    176.0   
10     77  18074428  2018-06-01 00:59:07  33.742860 -118.002675    135.0   
12     97  19880357  2018-06-01 00:59:03  33.769470 -118.269470    143.0   
13    109  18002801  2018-06-01 00:59:01  33.765600 -118.218530    241.0   

    SPEED PROBE_DATA_PROVIDER              X             Y  \
0    73.0             FLEET51  379816.173355  3.741709e+06   
9    32.0             FLEET51  381149.716844  3.747246e+06   
10   68.0             FLEET51  407125.235492  3.734097e+06   
12   13.0             FLEET51  382447.753699  3.737320e+06   
13   15.0             FLEET51  387159.976894  3.736834e+06   

                  LOCAL_TIME   unix_time  
0  2018-05-31 17:57:59-07:00  1527814679  
9  2018-05-31 17:59:08-07:00  1527814748  
10 2018-05-31 17:59:07-07:00  1527814747  
12 2018-05-31 17:59:03-07:00  1527814743  
13 2018-05-31 17:59:01-07:00  1527814741

In [9]:
unique = FLEET51['PROBE_ID'].unique()
len(unique)
len(FLEET51)

357286

In [10]:
unique_time = FLEET51['LOCAL_TIME'].unique()
len(unique_time)

77618

## Create Test Animation

In [11]:
from plotly.offline import init_notebook_mode, iplot
from IPython.display import display, HTML

In [23]:
# Extract unix time in list
unix_time = list(FLEET51.unix_time)
print('length of time list',len(unix_time))
print('length of unique times',len(set(unix_time)))

length of time list 357286
length of unique times 77618


In [55]:
test = unix_time[:10]


In [63]:
# make figure
figure = {
    'data': [],
    'layout': {},
    'frames': []
}

# fill in most of layout
figure['layout']['xaxis'] = {'title': 'Longitudinal Coordinate'}
figure['layout']['yaxis'] = {'title': 'Latitudinal Coordinate'}
figure['layout']['hovermode'] = 'closest'
figure['layout']['sliders'] = {
    'args': [
        'transition', {
            'duration': 400,
            'easing': 'cubic-in-out'
        }
    ],
    'initialValue': '17:00:00',
    'plotlycommand': 'animate',
    'values': unix_time,
    'visible': True
}
figure['layout']['updatemenus'] = [
    {
        'buttons': [
            {
                'args': [None, {'frame': {'duration': 500, 'redraw': False},
                         'fromcurrent': True, 'transition': {'duration': 300, 'easing': 'quadratic-in-out'}}],
                'label': 'Play',
                'method': 'animate'
            },
            {
                'args': [[None], {'frame': {'duration': 0, 'redraw': False}, 'mode': 'immediate',
                'transition': {'duration': 0}}],
                'label': 'Pause',
                'method': 'animate'
            }
        ],
        'direction': 'left',
        'pad': {'r': 10, 't': 87},
        'showactive': False,
        'type': 'buttons',
        'x': 0.1,
        'xanchor': 'right',
        'y': 0,
        'yanchor': 'top'
    }
]

# sliders_dict = {
#     'active': 0,
#     'yanchor': 'top',
#     'xanchor': 'left',
#     'currentvalue': {
#         'font': {'size': 20},
#         'prefix': 'Year:',
#         'visible': True,
#         'xanchor': 'right'
#     },
#     'transition': {'duration': 300, 'easing': 'cubic-in-out'},
#     'pad': {'b': 10, 't': 50},
#     'len': 0.9,
#     'x': 0.1,
#     'y': 0,
#     'steps': []
# }

In [65]:
# make frames
for time in test:
    frame = {'data': [], 'name': str(time)}

    
    Lat_by_time = list(FLEET51.loc[FLEET51['unix_time'] == time, 'LAT'])
    Long_by_time = list(FLEET51.loc[FLEET51['unix_time'] == time, 'LONG'])

    data_dict = {
        'x': Long_by_time,
        'y': Lat_by_time,
        'mode': 'markers',
        'name': 'FLEET51'
    }

    frame['data'].append(data_dict)
    
    figure['frames'].append(frame)
    



In [66]:
iplot(figure)

ValueError: 
    Invalid value of type 'builtins.dict' received for the 'sliders' property of layout
        Received value: {'args': ['transition', {'duration': 400, 'easing': 'cubic-in-out'}], 'initialValue': '17:00:00', 'plotlycommand': 'animate', 'values': [1527814679, 1527814748, 1527814747, 1527814743, 1527814741, 1527814736, 1527814736, 1527814736, 1527814736, 1527814734, 1527814732, 1527814726, 1527814725, 1527814680, 1527814691, 1527814685, 1527814678, 1527814673, 1527814676, 1527814676, 1527814666, 1527814666, 1527814665, 1527814664, 1527814418, 1527814280, 1527814619, 1527814616, 1527814585, 1527814580, 1527814578, 1527814575, 1527814575, 1527814572, 1527814564, 1527814563, 1527814317, 1527814568, 1527814566, 1527814566, 1527814564, 1527814561, 1527814561, 1527814557, 1527814557, 1527814548, 1527814547, 1527814547, 1527814537, 1527814535, 1527814548, 1527814544, 1527814540, 1527814521, 1527814526, 1527814532, 1527814529, 1527814526, 1527814523, 1527814523, 1527814521, 152781